# ComponentArrays
https://github.com/SciML/ComponentArrays.jl are array blocks that can be accessed through a named index.
You can compose differential equations without ModelingToolkit.

In [1]:
using ComponentArrays
using OrdinaryDiffEq
using SimpleUnPack: @unpack

tspan = (0.0, 20.0)

# Lorenz system
function lorenz!(D, u, p, t; f=0.0)
    @unpack σ, ρ, β = p
    @unpack x, y, z = u

    D.x = σ*(y - x)
    D.y = x*(ρ - z) - y - f
    D.z = x*y - β*z
    return nothing
end

lorenz_p = (σ=10.0, ρ=28.0, β=8/3)
lorenz_ic = ComponentArray(x=1.0, y=0.0, z=0.0)
lorenz_prob = ODEProblem(lorenz!, lorenz_ic, tspan, lorenz_p)


# Lotka-Volterra system
function lotka!(D, u, p, t; f=0.0)
    @unpack α, β, γ, δ = p
    @unpack x, y = u

    D.x =  α*x - β*x*y + f
    D.y = -γ*y + δ*x*y
    return nothing
end

lotka_p = (α=2/3, β=4/3, γ=1.0, δ=1.0)
lotka_ic = ComponentArray(x=1.0, y=1.0)
lotka_prob = ODEProblem(lotka!, lotka_ic, tspan, lotka_p)

# Composed Lorenz and Lotka-Volterra system
function composed!(D, u, p, t)
    c = p.c #coupling parameter
    @unpack lorenz, lotka = u

    lorenz!(D.lorenz, lorenz, p.lorenz, t, f=c*lotka.x)
    lotka!(D.lotka, lotka, p.lotka, t, f=c*lorenz.x)
    return nothing
end

comp_p = (lorenz=lorenz_p, lotka=lotka_p, c=0.01)
comp_ic = ComponentArray(lorenz=lorenz_ic, lotka=lotka_ic)
comp_prob = ODEProblem(composed!, comp_ic, tspan, comp_p)

ODEProblem with uType ComponentArrays.ComponentVector{Float64, Vector{Float64}, Tuple{ComponentArrays.Axis{(lorenz = ViewAxis(1:3, Axis(x = 1, y = 2, z = 3)), lotka = ViewAxis(4:5, Axis(x = 1, y = 2)))}}} and tType Float64. In-place: true
Non-trivial mass matrix: false
timespan: (0.0, 20.0)
u0: ComponentVector{Float64}(lorenz = (x = 1.0, y = 0.0, z = 0.0), lotka = (x = 1.0, y = 1.0))

Solve problem
We can solve the composed system...

In [2]:
comp_sol = solve(comp_prob)

retcode: Success
Interpolation: 3rd order Hermite
t: 241-element Vector{Float64}:
  0.0
  6.181923459793355e-5
  0.0006800115805772691
  0.004299130644888261
  0.010835274422622885
  0.01959555343271236
  0.0316252322166906
  0.047427991793856386
  0.06799287907875844
  0.09424926634485992
  ⋮
 19.470984724131988
 19.56149826542021
 19.638571826913314
 19.71202349285504
 19.776111547247073
 19.842847075547546
 19.911770857107726
 19.98556258790879
 20.0
u: 241-element Vector{ComponentArrays.ComponentVector{Float64, Vector{Float64}, Tuple{ComponentArrays.Axis{(lorenz = ViewAxis(1:3, Axis(x = 1, y = 2, z = 3)), lotka = ViewAxis(4:5, Axis(x = 1, y = 2)))}}}}:
 ComponentVector{Float64}(lorenz = (x = 1.0, y = 0.0, z = 0.0), lotka = (x = 1.0, y = 1.0))
 ComponentVector{Float64}(lorenz = (x = 0.9993825332995702, y = 0.0017297323086565809, z = 5.3446465987803325e-8), lotka = (x = 0.9999594060148846, y = 0.9999999987452488))
 ComponentVector{Float64}(lorenz = (x = 0.9932873611408131, y = 0.0189

In [3]:
map(comp_sol(0:0.1:20).u) do u
    u.lotka.x
end

201-element Vector{Float64}:
 1.0
 0.9365676111577816
 0.8792888862135674
 0.8317131775607912
 0.7981623360172602
 0.7657794013009516
 0.7244491807705086
 0.6818931117860487
 0.6418920515039641
 0.6050346686175818
 ⋮
 3.463870472793916
 3.6773336686361615
 3.8947925428201797
 4.110486391957825
 4.314781179879635
 4.498597362739154
 4.654513152532488
 4.75781342700078
 4.769017950232028

...or we can unit test one of the component systems

In [4]:
lotka_sol = solve(lotka_prob)
lotka_sol(1.0).x

0.5742850840860039

Symbolic mapping in `ODEFunction` using `syms=...`
Only available in non-nested ComponentArrays

In [5]:
lotka_func = ODEFunction(lotka!; syms=keys(lotka_ic))
lab_sol = solve(ODEProblem(lotka_func, lotka_ic, tspan, lotka_p))
lab_sol(1.0, idxs=:x)

0.5742850840860039

---

*This notebook was generated using [Literate.jl](https://github.com/fredrikekre/Literate.jl).*